In [ ]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis, QuadraticDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.svm import SVC
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import roc_auc_score
from imblearn.over_sampling import SVMSMOTE
from sklearn.feature_selection import SelectKBest, mutual_info_classif

import warnings
warnings.filterwarnings('ignore')


загрузим и выведем информацию о тренировочных и тестовых данных 

In [743]:
train_data = pd.read_csv("train.csv")
test_data = pd.read_csv("test.csv")
number_of_elements = 20000 
train_data = train_data.sample(n=number_of_elements,
                                        replace=False) 
train_data.info()
test_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20000 entries, 118808 to 100221
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   id                    20000 non-null  int64  
 1   Gender                20000 non-null  object 
 2   Age                   20000 non-null  int64  
 3   Driving_License       20000 non-null  int64  
 4   Region_Code           20000 non-null  float64
 5   Previously_Insured    20000 non-null  int64  
 6   Vehicle_Age           20000 non-null  object 
 7   Vehicle_Damage        20000 non-null  object 
 8   Annual_Premium        20000 non-null  float64
 9   Policy_Sales_Channel  20000 non-null  float64
 10  Vintage               20000 non-null  int64  
 11  Response              20000 non-null  int64  
dtypes: float64(3), int64(6), object(3)
memory usage: 2.0+ MB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 152862 entries, 0 to 152861
Data columns (total 11 columns):
 # 

In [744]:

train_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20000 entries, 118808 to 100221
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   id                    20000 non-null  int64  
 1   Gender                20000 non-null  object 
 2   Age                   20000 non-null  int64  
 3   Driving_License       20000 non-null  int64  
 4   Region_Code           20000 non-null  float64
 5   Previously_Insured    20000 non-null  int64  
 6   Vehicle_Age           20000 non-null  object 
 7   Vehicle_Damage        20000 non-null  object 
 8   Annual_Premium        20000 non-null  float64
 9   Policy_Sales_Channel  20000 non-null  float64
 10  Vintage               20000 non-null  int64  
 11  Response              20000 non-null  int64  
dtypes: float64(3), int64(6), object(3)
memory usage: 2.0+ MB


In [745]:
print(train_data)

            id  Gender  Age  Driving_License  Region_Code  Previously_Insured  \
118808  281364  Female   34                1         28.0                   0   
54162   283247    Male   74                1         29.0                   0   
120438   48343    Male   55                0         29.0                   0   
160817   33318  Female   22                1         11.0                   1   
44018   143472    Male   77                1         28.0                   0   
...        ...     ...  ...              ...          ...                 ...   
97874   497078  Female   26                1         29.0                   1   
37874   129070  Female   23                1         27.0                   0   
172026   49845  Female   43                1         11.0                   0   
126534  347641  Female   22                1         33.0                   1   
100221   73753    Male   50                1          6.0                   0   

       Vehicle_Age Vehicle_

Предварительная обработка данных 

In [746]:
ids = test_data["id"]
key = 'Response'
train_data

id  Gender  Age  Driving_License  Region_Code  Previously_Insured  \
118808  281364  Female   34                1         28.0                   0   
54162   283247    Male   74                1         29.0                   0   
120438   48343    Male   55                0         29.0                   0   
160817   33318  Female   22                1         11.0                   1   
44018   143472    Male   77                1         28.0                   0   
...        ...     ...  ...              ...          ...                 ...   
97874   497078  Female   26                1         29.0                   1   
37874   129070  Female   23                1         27.0                   0   
172026   49845  Female   43                1         11.0                   0   
126534  347641  Female   22                1         33.0                   1   
100221   73753    Male   50                1          6.0                   0   

       Vehicle_Age Vehicle_Damage  Annual_Premium  Policy_Sales_Channel  \
118808    1-2 Year            Yes         41600.0                 124.0   
54162    > 2 Years            Yes         35984.0                  26.0   
120438    1-2 Year            Yes          2630.0                  26.0   
160817    < 1 Year             No         21589.0                 152.0   
44018    > 2 Years            Yes         50408.0                  26.0   
...            ...            ...             ...                   ...   
97874     < 1 Year             No         31785.0                 152.0   
37874     < 1 Year            Yes         26845.0                  26.0   
172026    1-2 Year            Yes         43578.0                  26.0   
126534    < 1 Year             No         37283.0                 152.0   
100221    1-2 Year            Yes         35961.0                 124.0   

        Vintage  Response  
118808      292         0  
54162        57         0  
120438      232         1  
160817      127         0  
44018       212         0  
...         ...       ...  
97874       175         0  
37874       170         0  
172026       75         1  
126534      275         0  
100221       97         0  

[20000 rows x 12 columns]

In [747]:

train_data = pd.get_dummies(train_data)

In [748]:

x = train_data.drop([key], axis=1)
y = train_data[key]
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3)
scaler_2 = StandardScaler()
scaler_2.fit(x_train)
x_train_2 = scaler_2.transform(x_train)
x_test_2 = scaler_2.transform(x_test)

In [749]:
feature_names = list(train_data.columns)[:-1]
sel_mi = SelectKBest(mutual_info_classif, k=8).fit(x, y)
features = list(zip(feature_names, sel_mi.get_support()))
print(features)
useful_features = ['id'] + [i[0] for i in features if i[1] == True]
print(useful_features)
x_new = x[useful_features].copy(deep=True)
x_train_new, x_test_new, y_train_new, y_test_new = train_test_split(x_new, y, test_size=0.3)
x_train_new = scaler_2.fit_transform(x_train_new)
x_test_new = scaler_2.transform(x_test_new)

x_new.head()



[('id', True), ('Age', True), ('Driving_License', False), ('Region_Code', False), ('Previously_Insured', True), ('Annual_Premium', False), ('Policy_Sales_Channel', True), ('Vintage', False), ('Response', False), ('Gender_Female', False), ('Gender_Male', True), ('Vehicle_Age_1-2 Year', True), ('Vehicle_Age_< 1 Year', False), ('Vehicle_Age_> 2 Years', True), ('Vehicle_Damage_No', True)]
['id', 'id', 'Age', 'Previously_Insured', 'Policy_Sales_Channel', 'Gender_Male', 'Vehicle_Age_1-2 Year', 'Vehicle_Age_> 2 Years', 'Vehicle_Damage_No']


id      id  Age  Previously_Insured  Policy_Sales_Channel  \
118808  281364  281364   34                   0                 124.0   
54162   283247  283247   74                   0                  26.0   
120438   48343   48343   55                   0                  26.0   
160817   33318   33318   22                   1                 152.0   
44018   143472  143472   77                   0                  26.0   

        Gender_Male  Vehicle_Age_1-2 Year  Vehicle_Age_> 2 Years  \
118808        False                  True                  False   
54162          True                 False                   True   
120438         True                  True                  False   
160817        False                 False                  False   
44018          True                 False                   True   

        Vehicle_Damage_No  
118808              False  
54162               False  
120438              False  
160817               True  
44018               False

теперь построим модель

In [751]:
models = {
    'Логистическая Регрессия': LogisticRegression(solver='liblinear'),
    'Метод Ближайших Соседей': KNeighborsClassifier(),
    'Наивный Байесовский Классификатор': GaussianNB(),
    'Линейный Дискриминантный Анализ': LinearDiscriminantAnalysis(),
    'Квадратичный Дискриминантный Анализ': QuadraticDiscriminantAnalysis(),
    'Машина Опорных Векторов': SVC()
}

params = {
    'Логистическая Регрессия': {"max_iter": [100],
                                 "solver": ['sag', 'saga', 'newton-cg'],
                                 "n_jobs": [-1]},
    'Метод Ближайших Соседей': {"n_neighbors": list(range(3, 7)),
                                 "weights": ["uniform", "distance"],
                                 "p": [1, 2, 3, 4]},  
    'Наивный Байесовский Классификатор': {},
    'Линейный Дискриминантный Анализ': {"solver":  ["svd", 'lsqr', "eigen"]},
    'Квадратичный Дискриминантный Анализ': {"reg_param": np.linspace(0, 1, num=101)},
    'Машина Опорных Векторов': {"kernel": ['poly'],
                                'probability': [True],
                                 "class_weight": ["balanced"],
                                 "max_iter": [-1]}
}
best_models = {}
for name, model in models.items():
    random_search = GridSearchCV(model, params[name], cv=5, scoring='roc_auc', n_jobs=-1)
    random_search.fit(x_train_new, y_train_new)  
    best_model = random_search.best_estimator_
    best_models[name] = best_model


   

In [752]:
print(best_models)

{'Логистическая Регрессия': LogisticRegression(n_jobs=-1, solver='sag'), 'Метод Ближайших Соседей': KNeighborsClassifier(n_neighbors=6, p=4), 'Наивный Байесовский Классификатор': GaussianNB(), 'Линейный Дискриминантный Анализ': LinearDiscriminantAnalysis(), 'Квадратичный Дискриминантный Анализ': QuadraticDiscriminantAnalysis(reg_param=0.09), 'Машина Опорных Векторов': SVC(class_weight='balanced', kernel='poly', probability=True)}


In [753]:
results = {}

smote = SVMSMOTE(
    sampling_strategy='auto',  
    random_state=1, 
    k_neighbors=5,
    m_neighbors=10,
    n_jobs=-1,
    svm_estimator = SVC()
)

smoted_x, smoted_y = smote.fit_resample(x_new, y)
for name, model in best_models.items():
    model.fit(smoted_x,  smoted_y)
    y_pred = model.predict_proba(smoted_x)[:,1]
    score = roc_auc_score(smoted_y, y_pred)
    results[name] = score  

print(results)

{'Логистическая Регрессия': 0.7254721927257207, 'Метод Ближайших Соседей': 0.9251121434411501, 'Наивный Байесовский Классификатор': 0.797081811217315, 'Линейный Дискриминантный Анализ': 0.9477844883366694, 'Квадратичный Дискриминантный Анализ': 0.9471754814248508, 'Машина Опорных Векторов': 0.7126148235674492}


In [754]:
best_model_name = max(results, key=results.get)
best_model = best_models[best_model_name]
print("Лучшая модель:", best_model_name)


Лучшая модель: Линейный Дискриминантный Анализ


In [755]:
print(best_model)

LinearDiscriminantAnalysis()


In [756]:
test_data=pd.get_dummies(test_data)
y_pred = best_model.predict_proba(test_data[useful_features])[:, 1]
submission = pd.DataFrame({'id': ids, 'Response': y_pred})

submission.to_csv('submission.csv', index=False)
print("Файл submission.csv сохранен.")


Файл submission.csv сохранен.


In [757]:
for i in y_pred:
    print(i)

0.004111644274678196
0.11114947487794496
0.4921668131112443
0.0053453893255451775
0.923194818461949
0.704267052066694
0.004293390279893733
0.4029072940038052
0.7996645158836528
0.7967895896403524
0.8716664834904446
0.0033716550297260327
0.5050281212941922
0.07849221702395337
0.004425328557571813
0.8708318542435524
0.0033765452222719746
0.9229986449924091
0.2194483435923829
0.5363265331920987
0.14703595838145858
0.016249352364122817
0.7817814553482446
0.9379089625701426
0.3134056683786624
0.008499499533302066
0.8753002077016047
0.015305431521797584
0.2741337058337099
0.6733215484590389
0.004281498118906988
0.0026842854809541474
0.9057853888221553
0.011006603483310349
0.21160211023620568
0.5375442089164146
0.9108074637743795
0.0022351304096380623
0.028269531916918476
0.005939923017214689
0.5869137524625245
0.3470008255626818
0.8402520137004265
0.6260283222429945
0.14550929908333346
0.03233330751887992
0.001219929459496292
0.06567011694685755
0.8885853242158793
0.6950899963256645
0.040972